In [0]:
# Fazer Pasta
# dbutils.fs.mkdirs(path)

# Remover Pasta/Arquivo
# dbutils.fs.rm(path, recurse=True)

In [0]:
%run
./98_entrypoints

In [0]:
# Bibliotecas
from pyspark.sql.functions import *
from pyspark.sql.types import *

# Extraindo Dados Brutos

## Calendar

In [0]:
df_raw_calendar = (spark.read.
                   option("multiline", "true").
                   option("quote", '"').
                   option("escape", '"').
                   csv(path_raw_calendar, header=True))
df_raw_calendar = df_raw_calendar.dropDuplicates()
df_raw_calendar.display()

In [0]:
df_raw_calendar.count()

In [0]:
df_raw_calendar.write.mode("overwrite").parquet(path_bronze_calendar)

## Listings

In [0]:
df_raw_listings = (spark.read.
               option("multiline", "true").
               option("quote", '"').
               option("escape", '"').
               csv(path_raw_listings, header=True))
df_raw_listings = df_raw_listings.dropDuplicates()
df_raw_listings.display()

In [0]:
df_raw_listings.count()

In [0]:
df_raw_listings.write.mode("overwrite").parquet(path_bronze_listings)

## Reviews

In [0]:
df_raw_reviews = (spark.read.
               option("multiline", "true").
               option("quote", '"').
               option("escape", '"').
               csv(path_raw_reviews, header=True))
df_raw_reviews = df_raw_reviews.dropDuplicates()
df_raw_reviews.display()

In [0]:
df_raw_reviews.count()

In [0]:
df_raw_reviews.write.mode("overwrite").parquet(path_bronze_reviews)

# Limpeza Listings

In [0]:
df_listings = spark.read.parquet(path_bronze_listings)
df_listings.display()

id listing_url scrape_id last_scraped source name description neighborhood_overview picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed latitude longitude property_type room_type accommodates bathrooms bathrooms_text bedrooms beds amenities price minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm number_of_reviews_l30d first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value license instant_bookable calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 321637 https://www.airbnb.com/rooms/321637 20240627045056 2024-06-27 city scrape NEW WORLD LODGINGS #Caledonia Room null null https://a0.muscache.com/pictures/5574044/1d716766_original.jpg 1641925 https://www.airbnb.com/users/show/1641925 Charles 2012-01-23 Rio de Janeiro, Brazil Born in Scotland. 
Studied at art college in England (Bath Academy of Art) and was later invited to Brazil by Museum of Modern Art (Rio de Janeiro), on a scholarship. Built my own house in Rio.
I teach at the School of Visual Arts in Rio de Janeiro and lecture around the country to universities, cultural Institutions and companies, on "Creative Thinking and Problem Solving". At present writing a book on the subject.
I am also Director of "Dynamic Encounters" International Art Workshops, project involved in interviewing creative personalities around the world.

My main hobby (non educational) is boatbuilding and sailing. 
I build wooden sailing boats and sail around the Guanabara Bay area.
Others hobbies include reading and research, building my house. Hobbies are so tied up with work that it's kind of difficult to separate them.
 N/A N/A 0% f https://a0.muscache.com/im/users/1641925/profile_pic/1327338672/original.jpg?aki_policy=profile_small https://a0.muscache.com/im/users/1641925/profile_pic/1327338672/original.jpg?aki_policy=profile_x_medium Botafogo 3 4 ['email', 'phone'] t f null Botafogo null -22.94187 -43.18707 Private room in home Private room 3 1.0 1 bath 1 3 ["Kitchen", "Breakfast", "Wifi", "Free parking on premises", "Dryer", "Washer"] $718.00 3 90 3 3 90 90 3.0 90.0 null t 30 60 90 365 2024-06-27 1 0 0 2012-02-21 2012-02-21 5.0 4.0 5.0 5.0 5.0 4.0 5.0 null f 3 0 3 0 0.01 882550 https://www.airbnb.com/rooms/882550 20240627045056 2024-06-28 city scrape Apartament Almirante AG1204 null null https://a0.muscache.com/pictures/prohost-api/Hosting-882550/original/90a2cca9-5312-4860-ba70-89cadbfbf49f.png 4581272 https://www.airbnb.com/users/show/4581272 Diogo Rio Habitat 2013-01-03 Rio de Janeiro, Brazil Olá, sou formado em administração de empresas. Trabalho no ramo da saúde a mais de 10 anos. Em 2012 comecei a gerenciar apartamentos e por isso, ofereço por aqui apartamentos por temporada no Rio de Janeiro, localizados na zona sul, próximo a praia. Chamamos nosso grupo de Rio Habitat.
Nosso objetivo é oferecer um lugar muito agradável e estamos em desenvolvimento de uma estrutura ao turista.
O grande bacana é que estou começando a conhecer pessoas por aqui.
Essa comunidade tem tudo a ver com o conceito que tento trazer para a minha vida pessoal e empresarial.
Não estou sozinho operando os apartamentos. Posso contar com uma equipe que me

In [0]:
# Colunas para remover strings: "\\$","\\%", ",", " "
tratar_antes = ["host_response_rate", "host_acceptance_rate", "price"]


numericos_int = ["host_id", "host_response_rate", "host_listings_count", "host_total_listings_count", 
                 "accommodates", "bedrooms", "beds", "minimum_nights", "maximum_nights", "minimum_minimum_nights", 
                 "maximum_minimum_nights", "minimum_maximum_nights", "maximum_maximum_nights", "availability_30", 
                 "availability_60", "availability_90", "availability_365", "number_of_reviews", "number_of_reviews_ltm", 
                 "number_of_reviews_l30d", "calculated_host_listings_count", "calculated_host_listings_count_entire_homes", 
                 "calculated_host_listings_count_private_rooms", "calculated_host_listings_count_shared_rooms"]

numericos_float = ["latitude", "longitude", "bathrooms", "price", "minimum_nights_avg_ntm", "maximum_nights_avg_ntm", 
                   "review_scores_rating", "review_scores_accuracy", "review_scores_cleanliness", "review_scores_checkin", 
                   "review_scores_communication", "review_scores_location", "review_scores_value", "reviews_per_month"]

numericos_long = ["id", "scrape_id"]

colunas_data = ["last_scraped", "host_since", "calendar_last_scraped", "first_review", "last_review"]

booleanos = ["host_is_superhost", "host_has_profile_pic", "host_identity_verified", "has_availability", "instant_bookable"]

listas = ["host_verifications", "amenities"]

Iteração nas colunas para tratamento:

* tratar_antes - remover "%", "$" "," e " "
* numericos_int - Transformar int
* numericos_float - Transformar para float
* numericos_long - Transformar para LongType (como int gera muitos números nulos)
* colunas_data - Convertido para formato "yyyy-MM-dd"
* booleanos - Convertido para Booleano
* listas - Mantido como string
* Colunas não informadas foram mantidas como string

In [0]:
df_new = df_listings

In [0]:
# Removendo caracteres

for i in tratar_antes:
    df_new = (df_new
            .withColumn(i, regexp_replace(col(i), "\\$", ""))
            .withColumn(i, regexp_replace(col(i), ",", ""))
            .withColumn(i, regexp_replace(col(i), " ", ""))
            .withColumn(i, regexp_replace(col(i), "\\%", "")))

In [0]:
# Tratamento colunas Integer
for i in numericos_int:
    df_new = df_new.withColumn(i, col(i).cast(IntegerType()))

In [0]:
# Transformar em Float
for i in numericos_float:
    df_new = df_new.withColumn(i, col(i).cast(FloatType()))

In [0]:
# Transformar em LongType
for i in numericos_long:
    df_new = df_new.withColumn(i, col(i).cast(LongType()))

In [0]:
# Transformar em Data
for i in colunas_data:
    df_new = df_new.withColumn(i, to_date(i, "yyyy-MM-dd"))

In [0]:
# Transformar em Booleanos
for i in booleanos:
    df_new = (df_new.withColumn(i, 
                                when(col(i) == "t", True).
                                when(col(i) == "f", False).
                                otherwise(None)
                                ))

In [0]:
df_listings.filter(df_listings.scrape_id == "N/A").count()

0

In [0]:
df_listings.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in booleanos]).display()

host_is_superhost host_has_profile_pic host_identity_verified has_availability instant_bookable 868 0 0 337 0

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in booleanos]).display()

host_is_superhost host_has_profile_pic host_identity_verified has_availability instant_bookable 868 0 0 337 0

# Limpeza Calendar

In [0]:
df_calendar = spark.read.parquet(path_bronze_calendar)
df_calendar.display()

In [0]:
df_calendar.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_calendar.columns]).display()

In [0]:
df_calendar.count() == 12652371

## Limpezas e Ajustes de Dados

* listing_id - alterar para tipo LongType (Para integer gera muitos números nulos, LongType aceita um range maior de digitos)
* date - alterar para tipo datetime
* available - alterar t para True e f para False. Alterar tipo para booleano
* price - remover cifraão e virgulas. Alterar tipo para float
* minimum_nights - alterar para tipo integer
* maximum_nights - alterar para tipo integer

As conversões serão feitas e depois o schema vai ser informado como um todo.


In [0]:
df_new = (df_calendar
               .withColumn("listing_id", col("listing_id").cast(LongType()))
               .withColumn("date", to_date("date", "yyyy-MM-dd"))
               .withColumn("available", 
                           when(col("available") == "t", True).
                           when(col("available") == "f", False).
                           otherwise(None))
               .withColumn("price", regexp_replace(col("price"), "\\$", ""))
               .withColumn("price", regexp_replace(col("price"), ",", ""))
               .withColumn("price", col("price").cast("float"))
               .withColumn("minimum_nights", col("minimum_nights").cast("integer"))
               .withColumn("maximum_nights", col("maximum_nights").cast("integer")))

df_new.display()


In [0]:
df_calendar.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_calendar.columns]).display()

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_new.columns]).display()

# Limpeza Reviews

In [0]:
df_reviews = spark.read.parquet(path_bronze_reviews)
df_reviews.display()

In [0]:
df_reviews.columns

In [0]:
df_new = (df_reviews
               .withColumn("listing_id", col("listing_id").cast(LongType()))
               .withColumn("id", col("id").cast(LongType()))
               .withColumn("date", to_timestamp("date", "yyyy-MM-dd"))
               .withColumn("reviewer_id", col("reviewer_id").cast(LongType())))

df_new.display()

In [0]:
df_reviews.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_reviews.columns]).display()

In [0]:
df_new.select([sum(when(col(c).isNull(), 1).otherwise(0)).alias(c) for c in df_new.columns]).display()